make stacking fault structures.

In [ ]:
from wizard.atoms import SymbolInfo
from wizard.calculator import MaterialCalculator
from calorine.calculators import CPUNEP


calc = CPUNEP('../../potentials/4-4-80/nep.txt')
symbol_infos = [
SymbolInfo('Ag', 'fcc', 4.148),
SymbolInfo('Al', 'fcc', 4.044),
SymbolInfo('Au', 'fcc', 4.155),
SymbolInfo('Cu', 'fcc', 3.628),
SymbolInfo('Ni', 'fcc', 3.512),
SymbolInfo('Pb', 'fcc', 5.029),
SymbolInfo('Pd', 'fcc', 3.938),
SymbolInfo('Pt', 'fcc', 3.964),
SymbolInfo('Cr', 'bcc', 2.850),
SymbolInfo('Mo', 'bcc', 3.164),
SymbolInfo('Ta', 'bcc', 3.319),
SymbolInfo('V',  'bcc', 2.997),
SymbolInfo('W',  'bcc', 3.185),
SymbolInfo('Mg', 'hcp', 3.199, 5.192),
SymbolInfo('Ti', 'hcp', 2.933, 4.655),
SymbolInfo('Zr', 'hcp', 3.236, 5.151)
]

for symbol_info in symbol_infos:
    if symbol_info.structure == 'fcc':
        atoms = symbol_info.create_bulk_atoms((1,1,1))
        material_calculator = MaterialCalculator(atoms, calc, symbol_info)
        material_calculator.stacking_fault(a = (1,0,1), b = (1,2,-1), miller='0', distance = symbol_info.lattice_constant[0]/2, nlayers= 12)
        material_calculator.stacking_fault(a = (1,1,0), b = (-1,1,0), miller='1', distance = symbol_info.lattice_constant[0]/2, nlayers= 12)
    elif symbol_info.structure == 'bcc':
        atoms = symbol_info.create_bulk_atoms((1,1,1))
        material_calculator = MaterialCalculator(atoms, calc, symbol_info)
        material_calculator.stacking_fault(a = (-1,1,1), b = (-1,1,-2), miller='0', distance = symbol_info.lattice_constant[0]/2, nlayers= 12)
        material_calculator.stacking_fault(a = (1,1,-1), b = (1,-1,0), miller='1', distance = symbol_info.lattice_constant[0]/2, nlayers= 12)
    else:
        atoms = symbol_info.create_bulk_atoms((1,1,1))
        material_calculator = MaterialCalculator(atoms, calc, symbol_info)
        material_calculator.stacking_fault(a = (1,-1,0), b = (1,0,0), miller='0', distance = 1.1 * symbol_info.lattice_constant[0], nlayers= 14)
        material_calculator.stacking_fault(a = (1,-2,0), b = (1,1,0), miller='1', distance = 0.45 * symbol_info.lattice_constant[0], nlayers= 14)

Got DFT and NEP results.

In [3]:
from calorine.calculators import CPUNEP
from ase.calculators.lammpslib import LAMMPSlib
from wizard.io import read_xyz
from ase.units import J
import json

symbols = ['Ag', 'Al', 'Au', 'Cu', 'Ni', 'Pb', 'Pd', 'Pt', 'Cr', 'Mo', 'Ta', 'V', 'W', 'Mg', 'Ti', 'Zr']
processes = ['0','1']
data = {symbol: {process: {'DFT':[], 'NEP':[]} for process in processes} for symbol in symbols}
train_set = read_xyz('ref.xyz')
train_set = [[train_set[i+j:i+j+11] for j in range(0, 22, 11)] for i in range(0, len(train_set), 22)]
for items in train_set:
    frames = items[0]
    DFT_results = []
    NEP_results = []
    box = frames[0].get_cell()
    S = (box[0][0] * box[1][1] - box[0][1] * box[1][0])
    for atoms in frames:
        atoms.calc = CPUNEP('../potentials/4-4-80/nep.txt')   
        formation_energies_dft = atoms.info['energy'] / S / 2 / J / 1e-20
        formation_energies_nep = atoms.get_potential_energy() / S / 2 / J / 1e-20
        DFT_results.append(formation_energies_dft)
        NEP_results.append(formation_energies_nep)   

    DFT_results = [DFT_result - DFT_results[0] for DFT_result in DFT_results]
    NEP_results = [NEP_result - NEP_results[0] for NEP_result in NEP_results]

    key = frames[0].symbols[0]
    data[key]['0']['DFT'] = DFT_results
    data[key]['0']['NEP'] = NEP_results

    frames = items[1]
    DFT_results = []
    NEP_results = []
    box = frames[0].get_cell()
    S = (box[0][0] * box[1][1] - box[0][1] * box[1][0])
    for atoms in frames:
        atoms.calc = CPUNEP('../potentials/4-4-80/nep.txt')   
        formation_energies_dft = atoms.info['energy'] / S / 2 / J / 1e-20
        formation_energies_nep = atoms.get_potential_energy() / S / 2 / J / 1e-20
        DFT_results.append(formation_energies_dft)
        NEP_results.append(formation_energies_nep)   

    DFT_results = [DFT_result - DFT_results[0] for DFT_result in DFT_results]
    NEP_results = [NEP_result - NEP_results[0] for NEP_result in NEP_results]

    key = frames[1].symbols[0]
    data[key]['1']['DFT'] = DFT_results
    data[key]['1']['NEP'] = NEP_results

with open('data.json', 'w') as f:
    json.dump(data, f)

In [5]:
%matplotlib inline
from matplotlib import pyplot as plt
from ase.data import chemical_symbols, reference_states
from sklearn.metrics import mean_absolute_error
import json

with open('data.json', 'r') as f:
    data = json.load(f)
    
crystal_structures = {s: r['symmetry'] if r is not None else None
                      for s, r in zip(chemical_symbols, reference_states)}

plt.rcParams['text.usetex'] = False
plt.rcParams['font.size'] = 15
fig, axes = plt.subplots(
    figsize = (60, 25),
    dpi = 400,
    nrows = 4,
    ncols = 8,
    sharex = False,
    sharey = False
)

for k, (species, item) in enumerate(data.items()):
    structure = crystal_structures[species]
    ax = axes[k // 8, k % 8]
    ax.title.set_text(species)
    ax.plot(item['0']['NEP'], 'o-', color='C0', label='UNEP_v1', fillstyle = 'none')
    ax.plot(item['0']['DFT'], '*', color='C1', label='DFT')
    error = mean_absolute_error(item['0']['DFT'], item['0']['NEP'])
    ax.text(0.3, 0.2, f'MAE-UNEP-v1={error} J/m^2', transform=ax.transAxes, fontsize=10, va='bottom')
    ax.legend(loc = 'upper left')
    ax.title.set_text(species)
    ax.set_ylabel('Stacking fault Energy (J/m^2)')

    ax = axes[k // 8 + 2, k % 8]
    ax.title.set_text(species)
    ax.plot(item['1']['NEP'], 'o-', color='C0', label='UNEP_v1', fillstyle = 'none')
    ax.plot(item['1']['DFT'], '*', color='C1', label='DFT')
    error = mean_absolute_error(item['0']['DFT'], item['0']['NEP'])
    ax.text(0.3, 0.2, f'MAE-UNEP-v1={error} J/m^2', transform=ax.transAxes, fontsize=10, va='bottom')
    ax.legend(loc = 'upper left')
    ax.set_ylabel('Stacking fault Energy (J/m^2)')

plt.show()